### Assignment 13:  Financial Statement Question-Answering with a Retrieval-Augmented Generation (RAG) System
---
Name: Shiqi Hu

GTID: 904061372

### Very Important Note Before You Run The Code Files:

As I used together ai's llm model, you must update your api

In [3]:
!pip install -r requirements.txt

### Sample Tickers
---

In [4]:
import pandas as pd
import random


STUDENT_ID: int = 904061372  # TODO
NUM_DOCS: int = 10


def get_sp500_tickers_wikipedia() -> list[str]:
    url = "https://en.wikipedia.org/wiki/List_of_S%26P_500_companies"
    tables = pd.read_html(url)
    sp500_table = tables[0]
    return sp500_table["Symbol"].tolist()


all_sp500_tickers = get_sp500_tickers_wikipedia()

random.seed(STUDENT_ID)
sampled_tickers = sorted(random.sample(all_sp500_tickers, NUM_DOCS))

with open("sampled_tickers.txt", "w") as f:
    f.write("\n".join(sampled_tickers))

### config
---

In [5]:
import os

ROOT_DIR: str = '.'

DATA_DIR: str = os.path.join(ROOT_DIR, 'data')
os.makedirs(DATA_DIR, exist_ok=True)
ORIGINAL_DATA_DIR: str = os.path.join(DATA_DIR, 'original')
os.makedirs(ORIGINAL_DATA_DIR, exist_ok=True)
PROCESSED_DATA_DIR: str = os.path.join(DATA_DIR, 'processed')
os.makedirs(PROCESSED_DATA_DIR, exist_ok=True)
VECTOR_STORE_DIR: str = os.path.join(DATA_DIR, 'vector_store')
os.makedirs(VECTOR_STORE_DIR, exist_ok=True)

EMBED_MODEL_NAME: str = "sentence-transformers/all-mpnet-base-v2"  # TODO
LLM_MODEL_NAME: str = "meta-llama/Llama-3-70b-chat-hf"  # TODO


### Data Downloading
---

In [ ]:
import os
import shutil
import random
from sec_edgar_downloader import Downloader
from config import ORIGINAL_DATA_DIR
from sample_tickers import get_sp500_tickers_wikipedia

# Constants
EMAIL_ADDRESS = "siki_hu@outlook.com"
NUM_DOCS = 10   # Number of complete 10-K filings required per ticker
STUDENT_ID = 904061372

# Get the current working directory
CURRENT_DIR = os.getcwd()

# Load the initial list of tickers from a file
with open("sampled_tickers.txt", "r") as f:
    sampled_tickers = [line.strip() for line in f.readlines()]

all_sp500_tickers = get_sp500_tickers_wikipedia()

# Initialize the Downloader
dl = Downloader(CURRENT_DIR, email_address=EMAIL_ADDRESS)

def clear_filing_folder(ticker):
    """
    Clears the entire 'sec-edgar-filings' folder.
    """
    filings_dir = os.path.join(CURRENT_DIR, "sec-edgar-filings")
    if os.path.exists(filings_dir):
        shutil.rmtree(filings_dir)
        # print(f"Cleared existing folder for {ticker}.")

def count_filing_folders(ticker):
    """
    Counts the number of valid 10-K filing folders for a specific ticker.
    """
    filings_dir = os.path.join("D:\8803_D\A13", "sec-edgar-filings", ticker, "10-K")
    if os.path.exists(filings_dir):
        return len([d for d in os.listdir(filings_dir) if os.path.isdir(os.path.join(filings_dir, d))])
    return 0

def resample_tickers(current_tickers):
    """
    Resamples tickers from the unprocessed ticker list.
    """
    global STUDENT_ID
    STUDENT_ID += 1
    random.seed(STUDENT_ID)
    remaining_tickers = list(set(all_sp500_tickers) - set(current_tickers))
    return random.sample(remaining_tickers, NUM_DOCS)

def process_tickers(tickers):
    """
    Core logic: downloading, validation, and resampling.
    """
    valid_tickers = []
    for ticker in tickers:
        # print(f"Processing ticker: {ticker}")
        
        # Download 10-K filings
        dl.get("10-K", ticker, after="2010-01-01", before="2020-01-01")
        
        # Validate the completeness of historical filings
        num_filings = count_filing_folders(ticker)
        # print(f"Number of filings for {ticker}: {num_filings}")
        
        if num_filings == 10:
            valid_tickers.append(ticker)
            # print(f"Ticker {ticker} is valid.")
        else:
            # print(f"Ticker {ticker} is invalid. Clearing and resampling...")
            clear_filing_folder(ticker)
            new_tickers = resample_tickers(tickers)
            with open("sampled_tickers.txt", "w") as f:
                    f.write("\n".join(new_tickers))
            return process_tickers(new_tickers)  # Restart processing
        
        if len(valid_tickers) == NUM_DOCS:
            break
    
    return valid_tickers

# Start processing
sampled_tickers = process_tickers(sampled_tickers)

# Move 'sec-edgar-filings' directory to the target ORIGINAL_DATA_DIR
src_dir = os.path.join(CURRENT_DIR, "sec-edgar-filings")  # Original location of 'sec-edgar-filings'
dest_dir = os.path.join(ORIGINAL_DATA_DIR, "sec-edgar-filings")  # Target directory
if os.path.exists(src_dir):
    # Remove destination directory if it exists to avoid conflicts
    if os.path.exists(dest_dir):
        shutil.rmtree(dest_dir)
    
    # Move the entire directory
    shutil.move(src_dir, dest_dir)
    # print(f"Moved 'sec-edgar-filings' to {dest_dir}.")


# Output results
# print(f"Valid tickers with complete 10-year history: {sampled_tickers}")


In [8]:
sampled_tickers

['MCHP', 'MAR', 'SBUX', 'VRSK', 'MSI', 'A', 'STT', 'PH', 'SRE', 'SPG']

In [9]:
STUDENT_ID

904061378

### Data Processing
---

In [11]:
import os
import re
from config import ORIGINAL_DATA_DIR, PROCESSED_DATA_DIR
from bs4 import BeautifulSoup
import shutil
from tqdm import tqdm

# # TODO: take the downloaded data from ORIGINAL_DATA_DIR,
# # clean the documents (extract text information,
# # remove boilerplate, etc.) and save the cleaned data
# # to PROCESSED_DATA_DIR in the following format.

def process_10k_files():
    """Process and organize 10-K files from ORIGINAL_DATA_DIR to PROCESSED_DATA_DIR"""
    
    # Get list of tickers from ORIGINAL_DATA_DIR
    sec_edgar_path = os.path.join(ORIGINAL_DATA_DIR, "sec-edgar-filings")
    tickers = [d for d in os.listdir(sec_edgar_path) if os.path.isdir(os.path.join(sec_edgar_path, d))]
    
    # Create PROCESSED_DATA_DIR if it doesn't exist
    os.makedirs(PROCESSED_DATA_DIR, exist_ok=True)
    
    for ticker in tqdm(tickers, desc="Processing tickers"):
        # Path to ticker's 10-K directory
        ticker_10k_path = os.path.join(sec_edgar_path, ticker, "10-K")
        
        # Get all filing folders
        filing_folders = os.listdir(ticker_10k_path)
        
        # Process each filing
        for folder in filing_folders:
            # Extract year from folder name (format: 000319201-19-000031)
            year_match = re.search(r'-(\d{2})-', folder)
            if year_match:
                year = "20" + year_match.group(1)
                
                # Create directory for this filing
                processed_dir = os.path.join(PROCESSED_DATA_DIR, f"{ticker}_{year}")
                os.makedirs(processed_dir, exist_ok=True)
                
                # Path to full submission file
                submission_file = os.path.join(ticker_10k_path, folder, "full-submission.txt")
                
                try:
                    # Read the submission file
                    with open(submission_file, 'r', encoding='utf-8', errors='ignore') as f:
                        content = f.read()
                    
                    # Extract and clean the content
                    cleaned_content = clean_10k_content(content)
                    
                    # Save cleaned content
                    output_file = os.path.join(processed_dir, "content.txt")
                    with open(output_file, 'w', encoding='utf-8') as f:
                        f.write(cleaned_content)
                        
                except Exception as e:
                    print(f"Error processing {ticker} {year}: {str(e)}")

def clean_10k_content(content):
    # Remove non-printable characters
    content = re.sub(r'[^\x20-\x7E\n]', '', content)
    
    # Extract main content
    content_parts = content.split('<', 1)
    if len(content_parts) > 1:
        content = '<' + content_parts[1]
    
    soup = BeautifulSoup(content, 'lxml')
    
    # 1. Remove standard noise elements
    for tag in soup(['script', 'style', 'meta', 'head', 'link']):
        tag.decompose()
    
    # 2. Remove SEC headers and footers 
    patterns_to_remove = [
        'UNITED STATES SECURITIES AND EXCHANGE COMMISSION',
        'FORM 10-K',
        r'EDGAR.*HEADER',
        'Commission file number',
        'CONFORMED SUBMISSION.*TYPE',
        'CONFORMED PERIOD.*REPORT'
    ]
    for pattern in patterns_to_remove:
        for element in soup.find_all(text=re.compile(pattern)):
            element.extract()
    
    # 3. Enhanced table processing 
    for table in soup.find_all('table'):
        # Only process tables with actual content
        if not table.get_text(strip=True):
            table.decompose()
            continue
            
        # Remove empty cells
        for cell in table.find_all(['td', 'th']):
            if not cell.get_text(strip=True):
                cell.decompose()
            
        # Clean cell formatting but preserve structure
        for tag in table.find_all(True):
            tag.attrs = {}  # Remove attributes but keep structure

    # 4. Improve paragraph handling
    for tag in soup.find_all(['p', 'div', 'tr']):
        # Add newline only if it doesn't end with one
        if not tag.get_text().strip().endswith('\n'):
            tag.append('\n')
    
    # 5. Preserve important section headers
    sections = []
    section_pattern = re.compile(r'(?:^|\n)(?:ITEM|Item)\s+\d+[A-Za-z]?\.(?:\s+|$)')
    for item_header in soup.find_all(text=section_pattern):
        sections.append(item_header.strip())
    
    # 6. Normalize whitespace
    text = soup.get_text(separator=' ')
    text = re.sub(r'\n\s*\n', '\n\n', text)
    text = re.sub(r'\s+', ' ', text)
    
    # 7. Final cleanup
    text = re.sub(r'(?<=[.!?])\s+(?=[A-Z])', '\n', text)  # Split sentences into paragraphs
    text = re.sub(r'\n{3,}', '\n\n', text)  # Remove excessive newlines
    
    important_content = "\n".join(sections) + "\n\n" + text
    return important_content.strip()

process_10k_files()

# # In terms of implementation, this part is the most flexible.
# # The bare minimum for this part (valued 5 points) is saving
# # the original documents in the format described before
# # without processing them. The remaining 10 points will be given
# # for the attempts to clean the data.

# # There is no objective criteria for the quality of cleaning.
# # As the first thing to try, we would suggest removing
# # html tags. However, tables in this case become a mess,
# # and it is very likely that an LLM would do better if
# # the html structure was preserved.

# # Please make reasonable efforts to manipulate HTML tags effectively,
# # remove unnecessary boilerplate content, and explore other
# # preprocessing techniques as deemed appropriate.

# # Possible scores:
# # [10 pts]         The processed documents is stored
# #                 in the aforementioned format.
# # [5 pts]       The format for the processed data
# #                 is not preserved.
# # [up to +10 pts] Some level of cleaning is done.

Processing tickers:   0%|          | 0/10 [00:00<?, ?it/s]C:\Users\siki_\AppData\Local\Temp\ipykernel_43396\2238587042.py:254: DeprecationWarning: The 'text' argument to find()-type methods is deprecated. Use 'string' instead.
  for element in soup.find_all(text=re.compile(pattern)):
C:\Users\siki_\AppData\Local\Temp\ipykernel_43396\2238587042.py:282: DeprecationWarning: The 'text' argument to find()-type methods is deprecated. Use 'string' instead.
  for item_header in soup.find_all(text=section_pattern):
Processing tickers: 100%|██████████| 10/10 [1:01:19<00:00, 367.99s/it]


### Vector Store Construction
---

In [12]:
import os
from llama_index.core.schema import TextNode
from llama_index.core.node_parser import SentenceSplitter
from llama_index.embeddings.huggingface import HuggingFaceEmbedding
from llama_index.vector_stores.chroma import ChromaVectorStore
from llama_index.core import VectorStoreIndex, StorageContext
import chromadb
from tqdm import tqdm
from typing import List
import re

from config import PROCESSED_DATA_DIR, VECTOR_STORE_DIR, EMBED_MODEL_NAME

import logging
logging.basicConfig(level=logging.INFO)
logger = logging.getLogger(__name__)

# TODO: take all the documents from PROCESSED_DATA_DIR, chunk them and
# store them in a vector database with a corresponding vector store index.
# This requires implementing get_all_nodes and get_file_chunks for
# chunking the documents and filling out the 'main'.

# We suggest sticking to the provided template for we believe it to be
# the simplest implementation way. Please, provide explanation if you
# find it necessary to change template.

# Get the embedding model for the vector store index given EMBED_MODEL_NAME.

# Initialize embedding model
embed_model = HuggingFaceEmbedding(model_name=EMBED_MODEL_NAME)

def get_file_chunks(file_dir: str) -> list[str] | list[TextNode]:
    """
    Given a {ticker}_{year} directory, this method should read the file in there
    and chunk it. The choice of chunking strategy is a part of this task. The most
    basic chunking (using SentenceSplitter) is valued 10 points. More advanced methods
    are valued up to 5 points.

    Splits a file's content into smaller logical chunks using a fixed window with overlap.
    
    Args:
        file_dir (str): The path to the file.
        chunk_size (int): Number of tokens per chunk.
        overlap (int): Number of overlapping tokens between consecutive chunks.

    Returns:
        list[TextNode]: List of chunks as TextNode instances.

    """
    # Read content.txt
    content_path = os.path.join(file_dir, "content.txt")
    with open(content_path, 'r', encoding='utf-8') as f:
        content = f.read()

    # Step 1: Split content into sentences
    sentence_splitter = SentenceSplitter()  
    sentences = sentence_splitter.split_text(content)
    
    # Step 2: Create fixed-window chunks with overlap
    chunks = []
    current_chunk = []
    current_size = 0
    
    for sentence in sentences:
        sentence_length = len(sentence)
        
        # If adding this sentence exceeds chunk_size
        if current_size + sentence_length > 512 and current_chunk:
            # Save current chunk
            chunks.append(" ".join(current_chunk))
            
            # Start new chunk with overlap
            # Find sentences to keep for overlap
            overlap_size = 0
            overlap_sentences = []
            # Collect sentences for overlap from the end of the current chunk
            for s in reversed(current_chunk):
                overlap_size += len(s)
                if overlap_size > 50:
                    break
                overlap_sentences.insert(0, s)
                
            # Initialize new chunk with overlap sentences
            current_chunk = overlap_sentences
            current_size = sum(len(s) for s in current_chunk)
        
        # Add the current sentence to the chunk
        current_chunk.append(sentence)
        current_size += sentence_length
    
    # Add the last chunk if it exists
    if current_chunk:
        chunks.append(" ".join(current_chunk))
    
    # Step 3: Create TextNodes from the chunks
    return [TextNode(text=chunk) for chunk in chunks]


def get_all_nodes(filings_dir: str) -> list[TextNode]:
    """
    Given the filings directory, it should go over the {ticker}_{year} directories
    and get chunks for each of them using get_file_chunks methods, followed by
    creating TextNode instances for each chunk (if they are not already created --
    that will depend on the get_file_chunks implementation) and adding metadata 
    as dictionary: {'ticker': [ticker], 'year': [year]}.

    Process all ticker_year directories and create nodes with metadata.

    Returns:
        list[TextNode]: List of all nodes with metadata.
    """
    all_nodes = []

    # Get all ticker_year directories
    dir_contents = os.listdir(filings_dir)
    
    for dir_name in tqdm(dir_contents, desc="Processing directories"):
        dir_path = os.path.join(filings_dir, dir_name)
        
        # Extract ticker and year from directory name
        ticker, year = dir_name.split('_')
        
        print(dir_path)

        # Get chunks for this filing
        nodes = get_file_chunks(dir_path)
        
        # Add metadata to each chunk
        for node in nodes:
            node.metadata = {
                'ticker': ticker,
                'year': year
            }
            
        # Extend the all_nodes list with the current nodes
        all_nodes.extend(nodes)
        logger.info(f"Processed {dir_name}: {len(nodes)} chunks")

    logger.info(f"Total nodes created: {len(all_nodes)}")
    return all_nodes     

if __name__ == '__main__':
    # TODO: initialize a database which stores all_nodes in VECTOR_STORE_DIR
    # and a corresponding vector store index. We recommend ChromaDB.

    # Create VECTOR_STORE_DIR if it doesn't exist
    os.makedirs(VECTOR_STORE_DIR, exist_ok=True)
     
    print("Getting nodes from processed files...")
    all_nodes = get_all_nodes(PROCESSED_DATA_DIR)
    print(f"Total nodes created: {len(all_nodes)}")

    # Initialize ChromaDB
    print("Initializing ChromaDB...")
    chroma_client = chromadb.PersistentClient(path=VECTOR_STORE_DIR)
    
    # Delete existing collection if it exists
    try:
        chroma_client.delete_collection("financial_filings")
    except Exception as e:
        print(f"Error deleting collection: {e}")
        
    collection = chroma_client.create_collection("financial_filings")
    
    # Create vector store
    print("Creating vector store...")
    vector_store = ChromaVectorStore(chroma_collection=collection, embed_model=embed_model)
    storage_context = StorageContext.from_defaults(vector_store=vector_store)
    
    # Create vector store index
    print("Creating vector store index...")
    vector_index = VectorStoreIndex(
        nodes=all_nodes,
        storage_context=storage_context,
        embed_model=embed_model
    )
    
    # Validate stored documents
    collection_data = collection.get()
    print(f"\nTotal documents stored: {len(collection_data['documents'])}")
    for doc, metadata in zip(collection_data['documents'][:3], collection_data['metadatas'][:3]):
        print(f"\nStored Document Preview: {doc[:200]}...")
        print(f"Metadata: {metadata}")

    print("\nVector store construction completed!")


# Possible scores:
# [15 pts]       Chunks are obtained using SentenceSplitter and stored
#                in a vector database in VECTOR_STORE_DIR.
# [<15 pts]      Some mistakes exist (full documents are store in the
#                vector database, the directory is wrong, etc.).
# [up to +5 pts] An advanced chunking method is applied
#                (better than SentenceSplitter).


INFO:sentence_transformers.SentenceTransformer:Load pretrained SentenceTransformer: sentence-transformers/all-mpnet-base-v2
INFO:sentence_transformers.SentenceTransformer:2 prompts are loaded, with the keys: ['query', 'text']


Getting nodes from processed files...


Processing directories:   0%|          | 0/100 [00:00<?, ?it/s]

.\data\processed\A_2010


INFO:__main__:Processed A_2010: 3766 chunks
Processing directories:   1%|          | 1/100 [00:32<53:53, 32.67s/it]

...

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]


Total documents stored: 255276

Stored Document Preview: 0001047469-10-010499.txt : 20101220 0001047469-10-010499.hdr.sgml : 20101220 10-K 1 a2201423z10-k.htm 10-K Table of Contents UNITED STATES SECURITIES AND EXCHANGE COMMISSION Washington, D.C. 20549 For...
Metadata: {'_node_content': '{"id_": "be7b6508-8dcf-4c01-b12a-34624668ac89", "embedding": null, "metadata": {"ticker": "A", "year": "2010"}, "excluded_embed_metadata_keys": [], "excluded_llm_metadata_keys": [], "relationships": {}, "text": "", "mimetype": "text/plain", "start_char_idx": null, "end_char_idx": null, "text_template": "{metadata_str}\\n\\n{content}", "metadata_template": "{key}: {value}", "metadata_seperator": "\\n", "class_name": "TextNode"}', '_node_type': 'TextNode', 'doc_id': 'None', 'document_id': 'None', 'ref_doc_id': 'None', 'ticker': 'A', 'year': '2010'}

Stored Document Preview: Large accelerated filer ý Accelerated filer o Non-accelerated filer o Smaller reporting company o (Do not check if a smaller repor

In [13]:
# Test
test_query = "What is the revenue for 2013?"
query_embedding = embed_model.get_text_embedding(test_query)
query_result = collection.query(
    query_embeddings=[query_embedding],
    where={"year": "2013"},
    n_results=5
)
print("Test Query Results:")
for doc in query_result['documents']:
    print(doc[:100])


Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Test Query Results:
["Revenues of $1,912 million in 2012 , $1,945 million in 2011 , and $1,841 million in 2010 ; 2.\nSegment financial results of $283 million in 2012 , $172 million in 2011 , and $252 million in 2010 . 2012 segment financial results consisted of segment income of $97 million from Asia, $68 million from the Americas (excluding the United States), $62 million from Continental Europe, $30 million from the United Kingdom and Ireland, $21 million from the Middle East and Africa, and $5 million from Australia. 2011 segment financial results included $86 million of timeshare-strategy impairment charges for our former Timeshare segment, consisting of $84 million from the Americas (excluding the United States) and $2 million from Europe; and 3.\nFixed assets of $491 million in 2012 and $402 million in 2011 .\nWe include fixed assets located outside the United States at year-end 2012 and year-end 2011 in the “Property and equipment” caption in our Balance Sheets.\nX - Details Na

### System
---

In [ ]:
import pandas as pd
import os
import torch
from llama_index.core import QueryBundle, VectorStoreIndex, StorageContext
from llama_index.core.schema import TextNode
from llama_index.embeddings.huggingface import HuggingFaceEmbedding
from llama_index.vector_stores.chroma import ChromaVectorStore
from llama_index.llms.huggingface import HuggingFaceLLM
from llama_index.core.postprocessor import LLMRerank
from llama_index.core.postprocessor import SimilarityPostprocessor
from llama_index.core import VectorStoreIndex, StorageContext
from llama_index.core.vector_stores import MetadataFilters
from llama_index.core import Settings

from transformers import AutoTokenizer, pipeline
import chromadb
from tqdm import tqdm
import time
import together

from config import VECTOR_STORE_DIR, EMBED_MODEL_NAME, LLM_MODEL_NAME

RETRIEVER_SIMILARITY_TOP_K: int = 5
RERANKER_CHOICE_BATCH_SIZE: int = 3
RERANKER_TOP_N: int = 1

# TODO: implement RAG pipline with metadata filtering and reranking.
# When initializing different object in the constructor, please make
# the objects protected, which is achieved by underscoring the beginning
# of the object, as in the example with the embedding model:
# self._embed_model = ...

# We suggest sticking to the provided template for we believe it to be
# the simplest implementation way. Please, provide explanation if you
# find it necessary to change template.


class RAGSystem:
    def __init__(self):
        # Check if GPU is available
        self.device = "cuda" if torch.cuda.is_available() else "cpu"
        print(f"Using device: {self.device}")
        
        # Initialize embedding model given EMBED_MODEL_NAME.
        try:
            self._embed_model = HuggingFaceEmbedding(model_name=EMBED_MODEL_NAME)  # TODO
        except RuntimeError as e:
            print(f"Error loading embedding model on GPU: {e}")
            print("Falling back to CPU...")
            self.device = "cpu"
            self._embed_model = HuggingFaceEmbedding(
                model_name=EMBED_MODEL_NAME,
                device="cpu",
            )

        # Initialize a vector database from the existing collection
        # in VECTOR_STORE_DIR and a corresponding vector store index.
        # We recommend ChromaDB. Embedding model should be the same
        # as for storing the nodes.
        # TODO

        # Initialize the client first
        self._chroma_client = chromadb.PersistentClient(path=VECTOR_STORE_DIR)

        # Get existing collection
        self._collection = self._chroma_client.get_collection("financial_filings")

        # Initialize 
        self._vector_store = ChromaVectorStore(chroma_collection=self._collection)
        storage_context = StorageContext.from_defaults(vector_store=self._vector_store)
        self._vector_index = VectorStoreIndex.from_vector_store(
            vector_store=self._vector_store,
            embed_model=self._embed_model
        )

        # Initialize LLM given LLM_MODEL_NAME.
        # Tip: for the pipeline to work correctly, it is likely
        # you will need to create a tokenizer for the model.
        # We suggest looking into AutoTokenizer.
        # TODO
        
        # As I will directly use together.Completion.create(), I donnot need to initialize LLM
        # Here I will set up my together api
        os.environ['TOGETHER_API_KEY'] = 'da33d4a825b3a69ebb4ce5760ea41fdab4ec7f47a2fc68ad2987c7782684fe0d'
        api_key = os.getenv("TOGETHER_API_KEY")
        if not api_key:
            raise ValueError("TOGETHER_API_KEY not found in environment variables")
        
        together.api_key = api_key

        # Initialize reranker. We suggest LLM-based reranker with
        # RERANKER_CHOICE_BATCH_SIZE nodes to consider from the retriever and
        # RERANKER_TOP_N documents to return.
        # TODO

        self._reranker = SimilarityPostprocessor(
            choice_batch_size=RERANKER_CHOICE_BATCH_SIZE,
            top_n=RERANKER_TOP_N,
        )

    def respond(self, query: str, ticker: str, year: str) -> tuple[str, TextNode]:
        """
        Given a questy, a ticker and a year, should return a response
        to the provided query for the given company in the given year and
        the most relevant node.

        Process query and return response with most relevant node.

        Args:
           query (str): The user's question
           ticker (str): Company ticker symbol
           year (str): Year to query
           
        Returns:
           tuple[str, TextNode]: Generated response and most relevant node
        """
        # Convert the given query string to a query bundle (most likely
        # required for correct work).
        query_bundle = QueryBundle(query)

        # Initialize metadata filters.
        # TODO

        # print(f"Searching for {ticker} documents from {year}...")

        metadata_filters = MetadataFilters(
                filters=[
                    {"key": "ticker", "value": ticker},
                    {"key": "year", "value": year}
                ]
            )

        # Initialize retriever from the vector store index
        # with the filters above and RETRIEVER_SIMILARITY_TOP_K.
        # TODO

        retriever = self._vector_index.as_retriever(
            similarity_top_k=RETRIEVER_SIMILARITY_TOP_K,
            filters=metadata_filters
        )

        nodes = retriever.retrieve(query_bundle)

        filtered_nodes = [
            node for node in nodes 
            if node.metadata.get("ticker") == ticker and 
               node.metadata.get("year") == year
        ]
 
        if not filtered_nodes:
            return "No relevant information found for this company and year.", None

        # Apply the reranker to the retrieved nodes and get
        # the best one.
        # TODO
        reranked_nodes = self._reranker.postprocess_nodes(
            filtered_nodes,
            query_bundle
        )
 
        if len(reranked_nodes) == 0:
            return "Failed to rank the retrieved documents.", None
                
        top_nodes = reranked_nodes[:2]

        # Merge the reranked nodes with the query and give it
        # to the LLM to get the response.
        # TODO

        # Generate response using context
        # Combine the top node texts for context
        context_text = " ".join(node.text for node in top_nodes if node.text)
        # max_context_length = 4096
        # context_text = context_text[:max_context_length]

        prompt = (
            f"Based on the following context, answer the question: {query}\n\n"
            f"Context from {ticker}'s {year} report:\n{context_text}\n\n"
            "Answer the question concisely in one sentence:"
        )

        for attempt in range(5):  # Retry up to 5 times
            try:
                response = together.Completion.create(
                    model=LLM_MODEL_NAME,
                    prompt=prompt,
                    max_tokens=100,
                    temperature=0.7,
                    top_p=0.9,
                    stop=["\n"]
                )
                response_text = response.choices[0].text.strip()
                return response_text, top_nodes
            except Exception as e:
                print(f"Attempt {attempt + 1} failed: {e}", flush=True)
                time.sleep(2 ** attempt)  # Exponential backoff
        return "LLM API failed after multiple attempts.", []


if __name__ == '__main__':
    # TODO: come up with 2 questions for each ticker based on the documents,
    # and evaluate the quality of both the retriever by the most relevant node provided
    # and the response. Implementing automatic evaluation techniques is not required,
    # we expect to see detailed analysis of the manual evaluation.
    
    # Test questions for each ticker
    questions = [
        [
            {"query": "What is the total revenue of this company for this fiscal year?", "year": "2019"},
            {"query": "What is the gross profit of this company for this fiscal year?", "year": "2019"}
        ],
        [
            {"query": "Who is the Chairman of the Board of this company?", "year": "2015"},
            {"query": "What are the main risk factors of this company?", "year": "2015"}
        ],
        [
            {"query": "What are the main products of this company?", "year": "2017"},
            {"query": "What are the main revenue sources of this company?", "year": "2017"}
        ],
        [
            {"query": "What is the company's total debt for this fiscal year?", "year": "2010"},
            {"query": "What are the primary costs affecting the company's profitability?", "year": "2010"}
        ],
        [
            {"query": "What is the company's cash flow from operations for this fiscal year?", "year": "2013"},
            {"query": "What is the company's investment strategy mentioned in this year's report?", "year": "2013"}
        ],
        [
            {"query": "What are the key markets or regions where this company operates?", "year": "2019"},
            {"query": "What are the company's earnings per share (EPS) as reported?", "year": "2019"}
        ],
        [
            {"query": "What are the company's primary competitive advantages mentioned in the 10-K?", "year": "2018"},
            {"query": "What is the company's operating income for this fiscal year?", "year": "2018"}
        ],
        [
            {"query": "What is the total asset of this company for this fiscal year?", "year": "2017"},
            {"query": "What is the total shareholder's equity of this company for this fiscal year?", "year": "2017"}
        ],
        [
            {"query": "What is the net income of this company for this fiscal year?", "year": "2015"},
            {"query": "What is the fiscal year with year end of this 10K report?", "year": "2015"}
        ],
        [
            {"query": "What are the company's main subsidiaries mentioned in the 10-K?", "year": "2015"},
            {"query": "What are the company's capital expenditures for the reporting period?", "year": "2015"}
        ],
    ]

    ticker_file = "sampled_tickers.txt"
    with open(ticker_file, "r") as file:
        tickers = [line.strip() for line in file.readlines()]

    # Combine tickers with the questions
    test_cases = {ticker: questions[i % len(questions)] for i, ticker in enumerate(tickers)}

    # Initialize the RAG system
    system = RAGSystem()

    # Save results dynamically based on test cases
    results = []
    for ticker, queries in test_cases.items():
        for case in queries:
            query = case["query"]
            year = case["year"]
            response, nodes = system.respond(query, ticker, year)

            source_text = "\n\n".join(node.text for node in nodes if node.text)

            results.append({
                "ticker": ticker,
                "query": query,
                "year": year,
                "response": response,
                "retrieved nodes": source_text,
            })

            # # Print results to console
            # print(f"\nTicker: {ticker}")
            # print(f"Year: {year}")
            # print(f"Query: {query}")
            # print(f"Response: {response}")
            # print(f"Retrieved Nodes: {source_text[:500]}...\n")  # Truncate for readability

    # Save the results to a DataFrame and output to CSV
    results_df = pd.DataFrame(results)
    results_df.to_csv("query_results.csv", index=False, encoding="utf-8")

# Possible scores:
# [20 pts]        Basic RAG implemented, without metadata filtering
#                 and reranking.
# [+10 pts]       Metadata filtering implemented.
# [+5 pts]        Reranking implemented.
# [up to +10 pts] Manual evaluation implemented and analyzed.

Using device: cuda


C:\Users\siki_\AppData\Local\Temp\ipykernel_54920\148277839.py:184: DeprecationWarning: Call to deprecated function create.
  response = together.Completion.create(
c:\Users\siki_\anaconda3\envs\AI_in_Finance\Lib\site-packages\together\legacy\complete.py:68: UserWarning: The use of together.api_key is deprecated and will be removed in the next major release. Please set the TOGETHER_API_KEY environment variable instead.
  warnings.warn(API_KEY_WARNING)


In [32]:
evaluation_results =  pd.read_csv('query_results.csv')
evaluation_results

ticker                                              query  year  \
0    MCHP  What is the total revenue of this company for ...  2019   
1    MCHP  What is the gross profit of this company for t...  2019   
2     MAR  Who is the Chairman of the Board of this company?  2015   
3     MAR    What are the main risk factors of this company?  2015   
4    SBUX        What are the main products of this company?  2017   
5    SBUX  What are the main revenue sources of this comp...  2017   
6    VRSK  What is the company's total debt for this fisc...  2010   
7    VRSK  What are the primary costs affecting the compa...  2010   
8     MSI  What is the company's cash flow from operation...  2013   
9     MSI  What is the company's investment strategy ment...  2013   
10      A  What are the key markets or regions where this...  2019   
11      A  What are the company's earnings per share (EPS...  2019   
12    STT  What are the company's primary competitive adv...  2018   
13    STT  What is the company's operating income for thi...  2018   
14     PH  What is the total asset of this company for th...  2017   
15     PH  What is the total shareholder's equity of this...  2017   
16    SRE  What is the net income of this company for thi...  2015   
17    SRE  What is the fiscal year with year end of this ...  2015   
18    SPG  What are the company's main subsidiaries menti...  2015   
19    SPG  What are the company's capital expenditures fo...  2015   

                                             response  \
0   The total revenue of this company for this fis...   
1   The gross profit of this company for this fisc...   
2   The Chairman of the Board of this company is J...   
3   The main risk factors of this company include ...   
4   The main products of this company are coffee b...   
5   The main revenue sources of this company are c...   
6   The company's total debt for this fiscal year ...   
7   The primary costs affecting the company's prof...   
8   The company's cash flow from operations for th...   
9   The company's investment strategy is to invest...   
10  The key markets or regions where this company ...   
11  The company's earnings per share (EPS) as repo...   
12  State Street's primary competitive advantages ...   
13  The company's operating income for this fiscal...   
14  The total asset of this company for this fisca...   
15  The total shareholder's equity of this company...   
16  The net income of this company for the fiscal ...   
17  The fiscal year with year end of this 10K repo...   
18  The company's main subsidiaries mentioned in t...   
19  The company's capital expenditures for the rep...   

                                      retrieved nodes  
0   Note 21.\nQuarterly Results (Unaudited) The fo...  
1   Note 21.\nQuarterly Results (Unaudited) The fo...  
2   Carl T.\nBerquist Executive Vice President and...  
3   14 Table of Contents Item 1A.\nRisk Factors.\n...  
4   We believe, based on relationships established...  
5   Company-operated store revenues are reported n...  
6   Debt: The following table presents short-term ...  
7   There was also an increase in office maintenan...  
8   This reference is included to help users trans...  
9   font-size:10pt;">Within the equity securities ...  
10  The following table presents summarized inform...  
11  During the year ended October 31, 2018 , cash ...  
12  ; • our ability to create cost efficiencies th...  
13  Depletion and Amortization, Property, Plant, a...  
14  (a) Includes an investment in a joint venture ...  
15  30, 2017 Jun. 30, 2016 Jun. 30, 2015 Schedule ...  
16  SAN DIEGO GAS & ELECTRIC COMPANY CONSOLIDATED ...  
17  As provided in Internal Revenue Notice 2007-86...  
18  Disclosure - Quarterly Financial Data (Unaudit...  
19  font-family:Times New Roman;font-size: 10pt"> ...

### App
---

In [ ]:
import streamlit as st
from system import RAGSystem
import pandas as pd
import os
import traceback

# TODO: develop a Streamlit-based web application that enables
# users to ask questions about a company's financial statements
# for a specific year. The app should include dropdown menus for
# selecting the company ticker and year, alongside a text box for
# entering queries. Responses will be generated using a prebuilt
# Retrieval-Augmented Generation (RAG) pipeline.

# The application must be robust and should never crash, handling
# all errors gracefully with user-friendly messages. It should
# ensure a smooth user experience, even when unexpected issues
# occur during execution.

def load_tickers():
    """Load available tickers from file"""
    try:
        with open("sampled_tickers.txt", 'r') as file:
            return [line.strip() for line in file.readlines()]
    except Exception as e:
        st.error(f"Error loading tickers: {str(e)}")
        return []

def load_years():
    """Generate or load a list of available years dynamically"""
    return [str(year) for year in range(2010, 2020)]

def initialize_rag_system():
    """Initialize RAG system with error handling"""
    try:
        if 'rag_system' not in st.session_state:
            st.session_state.rag_system = RAGSystem()
        return st.session_state.rag_system
    except Exception as e:
        st.error(f"Failed to initialize RAG system: {str(e)}")
        st.error("Please check your configuration and try again.")
        return None

def main():
    st.title("Financial Statement Question-Answering System")
    
    # Initialize system
    rag_system = initialize_rag_system()
    if not rag_system:
        st.stop()
    
    # Sidebar for configuration
    with st.sidebar:
        st.header("Query Configuration")
        
        # Load and display ticker selection
        tickers = load_tickers()
        if not tickers:
            st.error("No tickers available")
            st.stop()
            
        ticker = st.selectbox(
            "Select Company Ticker",
            options=tickers
        )
        
        # Year selection
        years = load_years()
        if not years:
            st.error("No years available")
            st.stop()
        
        year = st.selectbox(
            "Select Year",
            options=years
        )
        
        # Display system status
        st.markdown("---")
        st.markdown("### System Status")
        st.markdown(f"Using device: {rag_system.device}")
        
    # Main content area
    col1, col2 = st.columns([2, 1])
    
    with col1:
        st.markdown("### Ask Questions")
        query = st.text_area(
            "Enter your question about the financial statements:",
            placeholder="e.g., What was the company's revenue?"
        )
        
        submit = st.button("Submit Question")
        
    # Handle query submission
    if submit and query:
        try:
            with st.spinner("Processing your question..."):
                response, node = rag_system.respond(query, ticker, year)
                
                # Display response
                st.markdown("### Response")
                st.write(response)
                
                # Display source information
                with col2:
                    st.markdown("### Source Information")
                    st.markdown("*Extracted from document:*")
                    if node:
                        if isinstance(node, list):  # Check if node is a list
                            # Combine texts from all nodes
                            source_text = "\n\n".join(n.text for n in node if n.text)
                            st.markdown(f"```\n{source_text[:500]}...\n```")  # Truncate if too long
                        elif hasattr(node, "text"):  # If it's a single node
                            st.markdown(f"```\n{node.text[:500]}...\n```")
                        else:
                            st.warning("No source text available")
                    else:
                        st.warning("No source document available")
        
        except Exception as e:
            st.error("An error occurred while processing your question.")
            st.error(f"Error details: {str(e)}")
            if st.checkbox("Show detailed error trace"):
                st.code(traceback.format_exc())
    
    # Additional Information
    with st.expander("Usage Tips"):
        st.markdown("""
        - Select a company ticker from the sidebar
        - Choose the year of interest
        - Enter your question about the financial statements
        - Click 'Submit Question' to get an answer
        - View the source information to understand where the answer came from
        """)

if __name__ == "__main__":
    try:
        main()
    except Exception as e:
        st.error("Application encountered an error. Please refresh the page.")
        st.error(f"Error details: {str(e)}")
        if st.checkbox("Show detailed error trace"):
            st.code(traceback.format_exc())



2024-11-30 15:10:30.453 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2024-11-30 15:10:30.459 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2024-11-30 15:10:30.467 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2024-11-30 15:10:30.471 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2024-11-30 15:10:30.473 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2024-11-30 15:10:30.474 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2024-11-30 15:10:30.476 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2024-11-30 15:10:30.478 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bar